<a href="https://colab.research.google.com/github/Mohamed28112003/Muffakir/blob/main/Muffakir_Mohamed_Khaled.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install  transformers
!pip install langchain
!pip install -U langchain-community
!pip install unstructured
!pip install "unstructured[pdf]"
!apt-get install -y poppler-utils
!pip install LangChain -q
!pip install -U langchain-community -q
!pip install langchain transformers
!pip install chromadb
!pip install sentence-transformers
!pip install langchain-nvidia-ai-endpoints
!pip install PyPDF2
!pip install rank-bm25 sentence-transformers
!pip uninstall nltk -y
!pip install nltk
!pip install openai
!pip install chromadb
!pip install groq
!pip install sentence-transformers
!pip install -U langchain-groq


In [ ]:
from transformers import AutoTokenizer
from langchain.text_splitter import CharacterTextSplitter
from transformers import AutoTokenizer, AutoModelForCausalLM

from langchain import PromptTemplate
from langchain.chains.question_answering import load_qa_chain
from langchain.llms import OpenAI
from dotenv import dotenv_values
from langchain.text_splitter import RecursiveCharacterTextSplitter, CharacterTextSplitter

from langchain.document_loaders import DirectoryLoader

import re
from langchain.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings


# Load TXT

In [ ]:
!pip uninstall nltk -y
!pip install nltk
import nltk
nltk.download('punkt')

Found existing installation: nltk 3.8.1
Uninstalling nltk-3.8.1:
  Successfully uninstalled nltk-3.8.1
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 25.1 MB/s eta 0:00:00


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

علشان لو في اكتر من فايل

In [ ]:


llm_loader = DirectoryLoader("/content/drive/MyDrive/Data/حقوق /عين شمس /رابعه/TXT",
                             glob="*.txt",
                             show_progress=True)

# Load all the documents
llm_data = llm_loader.load()

# Access the loaded data
print(llm_data)


100%|██████████| 10/10 [02:22<00:00, 14.27s/it]

[Document(metadata={'source': '/content/drive/MyDrive/Data/حقوق /عين شمس /رابعه/TXT/الاختصاص القضائي د.مينا عادل.txt'}, page_content='Total pages: 137\n\nPage number: 1\n\nالقانون الدولي الخاص\n\nالنظرية العامة\n\nلاختصاص القضائي الدولي\n\nدكتور\n\nمينا عادل زاهر\n\nمدرس القانون الدولى الخاص\n\nكلية الحقوق\n\nجامعة عين شمس\n\n2024\n\n2025\n\nPage number: 2\n\nPage number: 3\n\nمقدمة يلعب القانون الدولى الخاص دوراً هاماً فى مجال العلاقات الخاصة الدولية ، خاصةً بعد ظهور فكرة العولمة والتطور التكنولوجى ثم ازدات أهمية القانون الدولى الخاص بعد توسع التجارة الدولية مع تطور وسائل النقل البرى والبحرى والجوى مما أدى إلى سهولة انتقال الأفراد بين مختلف الدول. وقد ترتب على ذلك زيادة المعاملات بين الأشخاص ذوى الجنسيات المختلفة ومن هنا تأتى الحاجة إلى القانون الدولى الخاص لتحديد القانون الواجب التطبيق على العلاقة القانونية بالإضافة إلى معرفة المحكمة المختصة بنظر الدعوى. من المعروف أن قواعد الاختصاص القضائي الدولي تهدف إلى فض التزاحم بين محاكم دول مختلفة تسعى جميعها للاختصاص بنظر النزاع وذلك عن طريق

In [ ]:
len(llm_data)

10

In [ ]:
print(llm_data[0].page_content)

# Spilting

In [ ]:


# Initialize the text splitter
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=1000,  # Adjust chunk size based on content length
    chunk_overlap=0,  # No overlap needed
    separators=["Page number"] # Split at answer or next question
)

# Split each document in llm_data
split_documents = []
for doc in llm_data:
    chunks = text_splitter.split_text(doc.page_content)
    for chunk in chunks:
        split_documents.append({
            "metadata": doc.metadata,
            "content": chunk
        })

# Now split_documents contains the text chunks with their metadata


In [ ]:
len(split_documents)

In [ ]:




text_splitter_recursive = RecursiveCharacterTextSplitter(
    chunk_size=1000,  # Adjust chunk size based on content length
    chunk_overlap=0,  # No overlap needed
    separators=["Page number: /d+"] # Split at answer or next question
)

# Embeddding

In [ ]:
from langchain_community.embeddings import HuggingFaceEmbeddings

print("loading embedding model and index ....")

model_kwargs = {'device': 'cuda'}
encode_kwargs = {'normalize_embeddings': False}
embedding_model_id = "asafaya/bert-large-arabic"

embeddings = HuggingFaceEmbeddings(
    model_name = embedding_model_id,
    model_kwargs=model_kwargs,
    encode_kwargs=encode_kwargs
)

In [ ]:
from langchain.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.docstore.document import Document



# 2. Initialize ChromaDB vector store
persist_directory = "/content/chroma_db"  # Path where ChromaDB will be persisted
chroma_db = Chroma(persist_directory=persist_directory, embedding_function=embeddings)

# 3. Prepare your documents (assuming you already have them in `split_documents`)
#    Ensure that you only pass the `content` from the split documents
documents = [Document(page_content=doc['content'], metadata=doc['metadata']) for doc in split_documents]

# 4. Add documents to ChromaDB (this step will compute embeddings and store them in ChromaDB)
chroma_db.add_documents(documents)

# 5. Persist ChromaDB (optional, to save the embeddings to disk)
chroma_db.persist()

print("Embeddings stored successfully in ChromaDB!")


Embedding documents ....
Documents and embeddings have been stored in ChromaDB.




* upload DP



In [ ]:
!unzip /content/chroma_db.zip -d /content/chroma_db


Archive:  /content/chroma_db.zip
   creating: /content/chroma_db/content/chroma_db/
   creating: /content/chroma_db/content/chroma_db/f1e3e00e-5c6b-46f2-a0c1-0ac2f3fd730b/
  inflating: /content/chroma_db/content/chroma_db/f1e3e00e-5c6b-46f2-a0c1-0ac2f3fd730b/index_metadata.pickle  
  inflating: /content/chroma_db/content/chroma_db/f1e3e00e-5c6b-46f2-a0c1-0ac2f3fd730b/data_level0.bin  
  inflating: /content/chroma_db/content/chroma_db/f1e3e00e-5c6b-46f2-a0c1-0ac2f3fd730b/length.bin  
  inflating: /content/chroma_db/content/chroma_db/f1e3e00e-5c6b-46f2-a0c1-0ac2f3fd730b/header.bin  
  inflating: /content/chroma_db/content/chroma_db/f1e3e00e-5c6b-46f2-a0c1-0ac2f3fd730b/link_lists.bin  
  inflating: /content/chroma_db/content/chroma_db/chroma.sqlite3  


In [ ]:


# # Initialize the same embedding model you used earlier
# model_kwargs = {'device': 'cuda'}
# encode_kwargs = {'normalize_embeddings': False}
# embedding_model_id = "asafaya/bert-large-arabic"

# embeddings = HuggingFaceEmbeddings(
#     model_name=embedding_model_id,
#     model_kwargs=model_kwargs,
#     encode_kwargs=encode_kwargs
# )

# Path to the persisted ChromaDB
persist_directory = "/content/chroma_db"

# Reload ChromaDB
chroma_db = Chroma(persist_directory=persist_directory, embedding_function=embeddings)

print("ChromaDB loaded successfully!")


ChromaDB loaded successfully!


العب بقي من اول هنا 😲
Prompt
query
model
output


In [ ]:
import os
from langchain_groq import ChatGroq
from langchain.schema import HumanMessage  # Import HumanMessage

# Set the GROQ API Key as an environment variable
os.environ["GROQ_API_KEY"] = "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"

# Initialize the ChatGroq model
llm = ChatGroq(
    api_key=os.getenv("GROQ_API_KEY"),  # Retrieve the API key from the environment variable
    model="llama-3.1-70b-versatile",
    temperature=0.7,
    max_tokens=1024,
)

# Create a list of messages using the HumanMessage class
messages = [
    HumanMessage(content="Hello")
]

# Sending a message to the model
response = llm.invoke(messages)  # Use invoke instead of call

# Handle streaming response
for chunk in response:
    # Assuming the structure is (content, metadata), modify according to actual structure
    content = chunk[0] if isinstance(chunk, tuple) else chunk
    print(content or "", end="")


contentadditional_kwargsresponse_metadatatypenameidexampletool_callsinvalid_tool_callsusage_metadata

In [ ]:
print(response)

content="Hello, it's nice to meet you. Is there something I can help you with or would you like to chat?" additional_kwargs={} response_metadata={'token_usage': {'completion_tokens': 25, 'prompt_tokens': 36, 'total_tokens': 61, 'completion_time': 0.100206414, 'prompt_time': 0.008193942, 'queue_time': 0.007338876000000001, 'total_time': 0.108400356}, 'model_name': 'llama-3.1-70b-versatile', 'system_fingerprint': 'fp_9260b4bb2e', 'finish_reason': 'stop', 'logprobs': None} id='run-ce40d768-e9fb-401d-a148-97b41c7ea8a8-0' usage_metadata={'input_tokens': 36, 'output_tokens': 25, 'total_tokens': 61}


In [ ]:
#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

In [ ]:
qna_template = "\n".join([
    "Act as a knowledgeable legal analyst. Analyze the provided legal context and respond to the subsequent question with thoroughness and clarity. If the information needed to answer the question is not present in the context, respond with 'NO ANSWER IS AVAILABLE.'",
    "give the answer in details with egyptian accent ",

    "### Context",
    "{context}",

    "### Question",
    "{question}",

    "### Answer:",
])

qna_prompt = PromptTemplate(
    template=qna_template,
    input_variables=['context', 'question'],
    verbose=True
)

stuff_chain = load_qa_chain(llm, chain_type="stuff", prompt=qna_prompt)


In [ ]:
# Sample query
query = ''''


كلفت المحكمة الجنائية عضو النيابة العامة الحاضر في الجلسة بإجراء تحقيق
في دعوى معروضة أمامها. فقامت النيابة العامة بتنفيذ أمر المحكمة، وأجرت
التحقيق فيها أثناء سير المحاكمة. وبعد إجراء التحقيق عابت المحكمة على عضو
النيابة المحقق بسبب طريقة إجرائه لهذا التحقيق. فما رأيك في مسلك المحكمة؟

'''

# Generate the embedding for the query
query_embedding = embeddings.embed_query(query)

# Perform similarity search in ChromaDB
similar_documents = chroma_db.similarity_search_by_vector(query_embedding, k=5)

# Print the results
for doc in similar_documents:
    print("Content:", doc.page_content)
    print("Metadata:", doc.metadata)
    print("-" * 50)


In [ ]:
# Use the stuff chain to generate the answer
answer = stuff_chain(
    {
        "input_documents": similar_documents,  # Pass the search results directly
        "question": query  # Pass the original query
    },
    return_only_outputs=True,  # Return only the output from the chain
)

# Print the answer
print("Generated Answer:", answer)


Generated Answer: {'output_text': 'أنا الحقوقي، متشرف أن أجيبك في هذي القضية.\n\nبناءً على ما جاء في القضية، يبدو أن المحكمة الجنائية قد خالفت قواعد التنظيم القضائي. فمن المقرر أن النيابة العامة تعتبر جزءًا من السلطة القضائية، لكن ذلك لا يعني تبعيتها لقضاء الحكم أو خضوعها لإشرافه ورقابته. النيابة العامة هي سلطة اتهام مستقلة عن قضاء الحكم.\n\nوبناءً على ذلك، لا يجوز للمحكمة أن توجه النيابة العامة إلى اتباع إجراءات معينة، أو أن تقوم بدلاً عنها بأعمال تدخل في اختصاصها. ولا يجوز للمحكمة أن تكلف النيابة بإجراء تحقيق في دعوى معروضة عليها، لأنه يترتب على إحالة الدعوى من سلطة التحقيق على قضاء الحكم خروج الدعوى من حوزتها.\n\nومع ذلك، إذا استجابت النيابة العامة لأمر المحكمة وأجرت التحقيق في الدعوى أثناء سير المحاكمة، فإن هذا التحقيق يكون باطلا لمخالفته لقواعد التنظيم القضائي وهي متعلقة بالنظام العام.\n\nومن جهة أخرى، يبدو أن عيبة المحكمة على عضو النيابة المحقق بسبب طريقة إجرائه لهذا التحقيق تعد خرقًا لقواعد الاستقلال التي تتمتع بها النيابة العامة. فلا يجوز لمحكمة الموضوع انتقاد تصرفات النيابة ال

In [ ]:
print(answer)

{'output_text': 'بالطبع، سأجيب على السؤال بكل دقة ووضوح، مع استخدام اللهجة المصرية.\n\nالإجراءات الجنائية فى الدستور المصرى هى مجموعة من القواعد والقوانين التى تحكم الدعوى الجنائية فى مصر. ونصت الفقرة الأولى من المادة 49 من الدستور المصرى على أن "الدولة تتبع القانون، واستقلال القضاء، وحصانته، وحيادته، ضمانة أساسية لحماية الحقوق والحريات". ووفقاً لهذه المادة، فإن النيابة العامة هى جزء لا يتجزأ من القضاء، وتتولى التحقيق، وتحريبك، ومباشرة الدعوى الجنائية عدا ما يستثنيه القانون.\n\nومن الجدير بالذكر أن الدستور المصرى ينص على أن النيابة العامة هى سلطة مستقلة، ولا تتبع لأى جهة أخرى، ولهذا فإنها تتمتع بالاستقلال فى أدائها لوظائفها. ووفقاً للمادة 62 من قانون السلطة القضائية، فإن رجال النيابة العامة تابعون لرؤسائهم بترتيب درجتهم ثم للنائب العام، ولكن هذا لا يعنى أنهم غير مستقلين فى أدائهم لوظائفهم.\n\nكما أن الإجراءات الجنائية فى مصر تقوم على مبدأ العدالة، وضمان حقوق الأفراد، وحمايتهم من أى انتهاك. ولهذا فإن الإجراءات الجنائية هى مجموعة من القواعد والقوانين التى تحكم الدعوى الجنائية، وتضمن أن ي

In [ ]:
# Get the output text from the answer
output_text = answer['output_text']

# Print the formatted answer
print("Generated Answer:")
print("=" * 50)  # Separator line
print(output_text)


Generated Answer:
أنا الحقوقي، متشرف أن أجيبك في هذي القضية.

بناءً على ما جاء في القضية، يبدو أن المحكمة الجنائية قد خالفت قواعد التنظيم القضائي. فمن المقرر أن النيابة العامة تعتبر جزءًا من السلطة القضائية، لكن ذلك لا يعني تبعيتها لقضاء الحكم أو خضوعها لإشرافه ورقابته. النيابة العامة هي سلطة اتهام مستقلة عن قضاء الحكم.

وبناءً على ذلك، لا يجوز للمحكمة أن توجه النيابة العامة إلى اتباع إجراءات معينة، أو أن تقوم بدلاً عنها بأعمال تدخل في اختصاصها. ولا يجوز للمحكمة أن تكلف النيابة بإجراء تحقيق في دعوى معروضة عليها، لأنه يترتب على إحالة الدعوى من سلطة التحقيق على قضاء الحكم خروج الدعوى من حوزتها.

ومع ذلك، إذا استجابت النيابة العامة لأمر المحكمة وأجرت التحقيق في الدعوى أثناء سير المحاكمة، فإن هذا التحقيق يكون باطلا لمخالفته لقواعد التنظيم القضائي وهي متعلقة بالنظام العام.

ومن جهة أخرى، يبدو أن عيبة المحكمة على عضو النيابة المحقق بسبب طريقة إجرائه لهذا التحقيق تعد خرقًا لقواعد الاستقلال التي تتمتع بها النيابة العامة. فلا يجوز لمحكمة الموضوع انتقاد تصرفات النيابة العامة.

أخيرًا، يبدو أن مس